In [ ]:
import pandas as pd
import plotly.express as px

from utils.backtest import Portfolio, Timeline
from utils.data import nikkei_225
from utils.constants import DATE_FORMAT
from utils.dummy import (
    generate_stock_prices,
    get_quarterly_constituents,
    generate_signals,
    sort_basket,
)

In [ ]:
# Task 1:
# TODO: Get static historical Nikkei Constituents from Vinesh
start_date = "2010-01-01"
end_date = "2024-12-31"

# Nikkei 255 Constituents per quarter
constituents = get_quarterly_constituents(
    [stock["code"] for stock in nikkei_225], start_date, end_date
)

# Get all unique stocks that have been in Nikkei 225
stock_list = list(set([stock for stocks in constituents.values() for stock in stocks]))

In [ ]:
start_date = "2017-01-01"
end_date = "2022-12-31"

prices = generate_stock_prices(stock_list, start_date, end_date)
signal_series = generate_signals(constituents)

In [ ]:
def run_daily_backtest(
    prices,
    signal_series,
    asset_count=20,
    shorting_enabled=False,
):
    # pre-sort baskets on signals
    sorted_basket_series = {
        date: sort_basket(signals) for date, signals in signal_series.items()
    }

    price_df = pd.DataFrame(prices)
    dates = price_df.index

    initial_portfolio = Portfolio({}, {}, cash=1000.0)
    timeline = Timeline(dates[0], initial_portfolio)

    for i, date in enumerate(dates, start=1):
        # compute daily returns
        ret = price_df.loc[date] / price_df.shift(1).loc[date] - 1
        timeline.remark(date, ret)

        # rebalance periodically
        if date in signal_series:
            sorted_basket = sorted_basket_series[date]

            top = sorted_basket[:asset_count]
            bottom = sorted_basket[-asset_count:] if shorting_enabled else []
            timeline.rebalance(date, top, bottom)

    return timeline

In [ ]:
timeline = run_daily_backtest(
    prices, signal_series, asset_count=20, shorting_enabled=False
)

navs = timeline.get_navs()
print(f"Final NAV: {navs.iloc[-1]:.2f}")
print(f"Annualized Return: {timeline.calculate_annualized_return():.2%}")
print(f"Sharpe Ratio: {timeline.calculate_sharpe_ratio():.2f}")

Final NAV: 1187.17
Annualized Return: 2.80%
Sharpe Ratio: 0.05


In [ ]:
factor = "factor"
num_noise = 100

rebalance_days = 21
asset_count = 20

# container for all timelines
timelines = {}

# run the “factor” backtest
timelines[factor] = run_daily_backtest(
    prices,
    generate_signals(constituents),  # TODO: Use actual derived signals
    asset_count=asset_count,
    shorting_enabled=True,
)

# run N noise backtests
for i in range(num_noise):
    label = f"noise_{i}"
    timelines[label] = run_daily_backtest(
        prices,
        generate_signals(constituents),
        asset_count=asset_count,
        shorting_enabled=True,
    )

In [25]:
factor_cr = pd.Series(timelines[factor].get_cumulative_returns(), name=factor)

# noise series
noise_cr = [
    pd.Series(timelines[f"noise_{i}"].get_cumulative_returns(), name=f"noise_{i}")
    for i in range(num_noise)
]

df = pd.concat([factor_cr] + noise_cr, axis=1)

In [26]:
fig = px.line(
    df,
    y=[col for col in df.columns if col.startswith("noise_")],
    labels={"value": "Cumulative Return", "index": "Date"},
)

# style the noise traces
for trace in fig.data:
    trace.update(line=dict(color="black", width=2, dash="dot"), opacity=0.1)

# overlay the factor line on top
fig.add_scatter(
    x=df.index,
    y=df[factor],
    mode="lines",
    name=factor,
    line=dict(color="red", width=4),
    marker=dict(size=7, color="red"),
)

fig.update_layout(
    width=1000,
    height=600,
    hovermode="closest",
    showlegend=False,
)

fig.show()

In [27]:
print(f"Factor: {factor}")
print(f"Annualized Return: ", timelines[factor].calculate_annualized_return())
print(f"Sharpe Ratio:", timelines[factor].calculate_sharpe_ratio())

Factor: factor
Annualized Return:  -0.019140075538852885
Sharpe Ratio: -0.022064559094735963


In [ ]:
# Tasks to do:
# Make sense of the generated code - DONE
# Use the Nikkei 225 data instead - DONE
# Use the Nikkei 225 index instead - DONE


# Get Actual time series of prices
# Get Actual time series of signals # any
# Ask Vinesh for actual index constituents
# Use a valid signal like simple sentiment instead
# Use ELO score